In [87]:
import os
import json
import pandas as pd
import geopandas as gpd
from shapely.geometry.polygon import Polygon
from shapely.geometry.multipolygon import MultiPolygon

import json
import matplotlib as mpl
import pylab as plt
import string
import numpy as np

from bokeh.io import output_file, show, output_notebook, export_png
from bokeh.layouts import row, column, layout
from bokeh.models import CustomJS, GeoJSONDataSource, LogColorMapper, ColorBar, HoverTool
from bokeh.plotting import figure, save, output_file
from bokeh.palettes import brewer
from bokeh.tile_providers import CARTODBPOSITRON, CARTODBPOSITRON_RETINA, STAMEN_TONER, get_provider
from bokeh.models.widgets import Select
from bokeh.embed import autoload_static
from bokeh.resources import CDN

import plotly.express as px

## Read in the data

In [67]:
# Define the filepaths
home_dir = os.path.expanduser("~")
data_fp = "iec/shrug_covid"

# Read in the COVID data
df = pd.read_stata(os.path.join(home_dir, data_fp, "hospitals_dist_export.dta"))

# Read in the pc11 district shapefile
gdf = gpd.read_file(os.path.join(home_dir, "iec1", "gis", "pc11", "pc11-district.shp"))

# Rename columns to match pc11 keys
gdf = gdf.rename(columns = {"pc11_s_id": "pc11_state_id",
                            "pc11_d_id": "pc11_district_id"})


data = gdf.merge(df, left_on=["pc11_state_id", "pc11_district_id"], right_on=["pc11_state_id", "pc11_district_id"])

# convert multipoloygon states into individual polygons
data = data.explode()

# reduce resolution of polygons to make loading faster
data['geometry'] = data['geometry'].simplify(tolerance=0.01)

data['pc11_state_name'] = [string.capwords(x) for x in data['pc11_state_name']]
data['pc11_district_name'] = [string.capwords(x) for x in data['pc11_district_name']]

# calculate state avergage
state_avg = data.groupby(['pc11_state_id']).mean()[["dlhs4_perk_beds_pubpriv"]]
# find indices of missing district data
missing_index = data.loc[data['dlhs4_perk_beds_pubpriv'].isnull()].index
# fill in the missing districts with the state averages
data.loc[missing_index, "dlhs4_perk_beds_pubpriv"] = state_avg.loc[data.loc[missing_index, "pc11_state_id"], "dlhs4_perk_beds_pubpriv"].values

# convert to web mercator crs to match the basemap
data = data.to_crs(epsg=3857)

# write file to geojson
# data.to_file("/scratch/acampion/test.json", driver="GeoJSON")

## Plot the Data

In [52]:
def get_geodatasource(gdf,
                      index_columns=['pc11_state_name', 'pc11_state_id', 'pc11_district_name','pc11_district_id']):    
    """Get getjsondatasource from geopandas object""" 
    json_data = json.dumps(json.loads(gdf.to_json()))
    return GeoJSONDataSource(geojson = json_data)

def create_figure(title="", ph=850, pw=850):
    #-----# 
    # MAP #
    #-----# 
    # define tools
    tools = 'wheel_zoom, pan, reset'
    
    # define basemap
    tile_provider = get_provider(CARTODBPOSITRON_RETINA)

    # create figure
    p = figure(title = title,
               plot_height=ph ,
               plot_width=pw,
               x_axis_type="mercator",
               y_axis_type="mercator",
               toolbar_location='right',
               tools=tools)
    p.add_tile(tile_provider)
    p.xgrid.grid_line_color = None
    p.ygrid.grid_line_color = None
    return p


def plot_patch_data(geosource, df,
                    column="", column_label="data",
                    cmap="YlGnBu", cmap_res=8, cmap_r=True, 
                    title='', ph=850, pw=850,
                    leg_title=""):

    #-----------# 
    # COLOR BAR #
    #-----------# 
    # define the color palette
    palette = brewer[cmap][cmap_res]
    
    # reverese the color palette if desired
    if cmap_r == True:
        palette = palette[::-1]
    
    # extract data values for desired column
    vals = df[column]
    
    #Instantiate LogColorMapper that maps numbers in a range, into a sequence of colors.
    color_mapper = LogColorMapper(palette = palette, low = vals.min(), high = vals.max())
    
    # set the nan_color of the color mapper
    color_mapper.nan_color = "#f0f0f0"
    
    color_bar = ColorBar(color_mapper=color_mapper, label_standoff=8, width=int(pw*0.9), height=20,
                         location=(0,0), orientation='horizontal', title=leg_title)
    
    #------------#
    # CLOROPLETH #
    #------------#
    
    #Add patch renderer to figure
    patch = p.patches('xs','ys',
                      source=geosource,
                      fill_alpha=0.7,
                      line_width=0.5,
                      line_color='black', 
                      hover_fill_alpha=1.0,
                      hover_line_width=2.0,
                      hover_line_color='white',
                      fill_color={'field': column, 'transform': color_mapper}
                     )
    
    #create hover tool
    hover_tool = HoverTool(
        tooltips=[
            ("State", "@pc11_state_name"),
            ("District", "@pc11_district_name"),
            (column_label, "@"+ column +"{1.11}")
        ])
    
    return patch, color_bar, hover_tool


In [106]:
output_file("hospital-beds.html", title="Number of Hospital Beds per 1000")

# create figure
p = create_figure( title="Number of Hospital Beds per 1000")

geosource = get_geodatasource(data)
patch, color_bar, hover_tool = plot_patch_data(geosource, df,
                           column="dlhs4_perk_beds_pubpriv",
                           column_label="Hospital Beds per 1000 People",
                           title="Hospital Beds", leg_title="Number of Hospital Beds per 1000 People (log scale)")
p.patch
p.tools.append(hover_tool)
p.title.text_font_size = '16pt'
p.add_layout(color_bar, 'below')   

# write out the code to embed the figure
js, tag = autoload_static(p, CDN, 'main/static/main/js/hospital-beds.js')
with open('../assets/hospital-beds.js', 'w') as f:
        f.write(js)
with open("../assets/hospital-beds.html", "w") as file:
    file.write(tag)
            
save(p)
#export_png(p, filename="../assets/dlhs4_perk_beds_pubpriv.png", height=1200, width=1200)

## Read CFR Data

In [135]:
# Read in the COVID data
df = pd.read_stata(os.path.join(home_dir, data_fp, "district_age_dist_cfr.dta"))

# convert the estimated cfr to be centered at median district
df["district_estimated_cfr_t"] = df["district_estimated_cfr_t"]/(np.median(df["district_estimated_cfr_t"]))

# pc11 keys
pc11_keys = pd.read_stata(os.path.join(home_dir, "iec", "keys", "pc11_district_key.dta"))
df = df.merge(pc11_keys, left_on=["pc11_state_id", "pc11_district_id"], right_on=["pc11_state_id", "pc11_district_id"])

# Read in the pc11 district shapefile
gdf = gpd.read_file(os.path.join(home_dir, "iec1", "gis", "pc11", "pc11-district.shp"))

# Rename columns to match pc11 keys
gdf = gdf.rename(columns = {"pc11_s_id": "pc11_state_id",
                            "pc11_d_id": "pc11_district_id"})


data = gdf.merge(df, left_on=["pc11_state_id", "pc11_district_id"], right_on=["pc11_state_id", "pc11_district_id"])

# convert multipoloygon states into individual polygons
data = data.explode()

# reduce resolution of polygons to make loading faster
data['geometry'] = data['geometry'].simplify(tolerance=0.01)
data['pc11_state_name'] = [string.capwords(x) for x in data['pc11_state_name']]
data['pc11_district_name'] = [string.capwords(x) for x in data['pc11_district_name']]

# calculate state avergage
state_avg = data.groupby(['pc11_state_id']).mean()[["district_estimated_cfr_t"]]
# find indices of missing district data
missing_index = data.loc[data['district_estimated_cfr_t'].isnull()].index
# fill in the missing districts with the state averages
data.loc[missing_index, "district_estimated_cfr_t"] = state_avg.loc[data.loc[missing_index, "pc11_state_id"], "district_estimated_cfr_t"].values

# convert to web mercator crs to match the basemap
data = data.to_crs(epsg=3857)

In [137]:
output_file("mortality-pred.html", title="Mortality Prediction")

# create figure
p = create_figure( title="Mortality Prediction")

geosource = get_geodatasource(data)
patch, color_bar, hover_tool = plot_patch_data(geosource, df,
                           column="district_estimated_cfr_t",
                           column_label="Mortality Prediction",
                           title="Mortality Prediction",cmap="RdYlBu",cmap_r=False, cmap_res=10,
                           leg_title="Mortality Prediction, Median District is 1")
p.patch
p.tools.append(hover_tool)
p.add_layout(color_bar, 'below')   
p.title.text_font_size = '16pt'

# write out the code to embed the figure
js, tag = autoload_static(p, CDN, 'mortality-pred.js')
with open('../assets/mortality-pred.js', 'w') as f:
        f.write(js)
with open("../assets/mortality-pred.html", "w") as file:
    file.write(tag)
            
        
save(p)
#export_png(p, filename="../assets/district_estimated_cfr_t.png", height=1200, width=1200)


'/dartfs-hpc/rc/home/y/f00473y/ddl/covid/e/mortality-pred.html'

# Sandbox

Everything below here is under development and being used for testing but is not final code

### Get better color scaling

In [ ]:
column="dlhs4_perk_beds_pubpriv"
qcuts = pd.qcut(list(data[column].dropna()), 8)
data[f"{column}_cat"] = np.nan
data.loc[data[column].notnull(), f"{column}_cat"] = qcuts._codes

### JS callbacks in Bokeh

In [424]:
select = Select(title="Variables:", value="dlhs4_perk_beds_pubpriv", options=["dlhs4_perk_beds_pubpriv", "pc_perk_beds_tot"])

callback = CustomJS(args={'geosource':geosource},code="""
        // print the selectd value of the select widget - 
        // this is printed in the browser console.
        // cb_obj is the callback object, in this case the select 
        // widget. cb_obj.value is the selected value.
        console.log('changed selected variable', cb_obj.value);

        // create a new variable for the data of the column data source
        // this is linked to the plot
        var data = geosource.data;

        // allocate the selected column to the field for the y values
        data['val'] = data[cb_obj.value];

        // register the change - this is required to process the change in 
        // the y values
        geosource.change.emit();
""")

l = column(p, dropdown)

### Plotly

In [49]:
home_dir = os.path.expanduser("~")
data_fp = "iec/shrug_covid"

# Read in the COVID data
df = pd.read_stata(os.path.join(home_dir, data_fp, "hospitals_dist_export.dta"))

# Read in the pc11 district shapefile
gdf = gpd.read_file(os.path.join(home_dir, "iec1", "gis", "pc11", "pc11-district.shp"))

# Rename columns to match pc11 keys
gdf = gdf.rename(columns = {"pc11_s_id": "pc11_state_id",
                            "pc11_d_id": "pc11_district_id"})


data = gdf.merge(df, left_on=["pc11_state_id", "pc11_district_id"], right_on=["pc11_state_id", "pc11_district_id"])

# convert multipoloygon states into individual polygons
data = data.explode()

# reduce resolution of polygons to make loading faster
data['geometry'] = data['geometry'].simplify(tolerance=0.02)
data['pc11_state_name'] = [string.capwords(x) for x in data['pc11_state_name']]
data['pc11_district_name'] = [string.capwords(x) for x in data['pc11_district_name']]

data['dlhs4_perk_beds_pubpriv_log'] = np.log(data['dlhs4_perk_beds_pubpriv'] + 1)

In [50]:
data.to_file("/scratch/acampion/test.json", driver="GeoJSON")
with open("/scratch/acampion/test.json") as json_file:
    districts = json.load(json_file)

In [26]:
column="dlhs4_perk_beds_pubpriv"
qcuts = pd.qcut(list(data[column].dropna()), 8)
data[f"{column}_cat"] = np.nan
data.loc[data[column].notnull(), f"{column}_cat"] = qcuts._codes

In [60]:
fig = px.choropleth_mapbox(data,
                           geojson=districts,
                           locations='pc11_district_id',
                           color='dlhs4_perk_beds_pubpriv',
                           color_continuous_scale="YlGnBu_r",
                           range_color=(np.min(data['dlhs4_perk_beds_pubpriv']),
                                        np.max(data['dlhs4_perk_beds_pubpriv'])),
                           featureidkey="properties.pc11_district_id",
                           opacity=0.5,
                           labels={'dlhs4_perk_beds_pubpriv':'Number of Hospital Beds'},
                          )

fig.update_layout(mapbox_style="light",
                  mapbox_accesstoken=mapboxt,
                  mapbox_zoom=3,
                  mapbox_center = {"lat": 20.5937, "lon": 78.9629},
                  margin={"r":0,"t":0,"l":0,"b":0})

In [64]:
L = len(districts['features'])
for i in range(L):
    districts['features'][i]['id'] = f'{i}'

In [81]:
varlist = ["dlhs4_perk_beds_pubpriv", "pc_perk_beds_tot"]
all_vars = []        
label_dict = {"dlhs4_perk_beds_pubpriv": "Number of Hospital Beds",
               "pc_perk_beds_tot": "Something"}

for var in varlist:
    fig = px.choropleth_mapbox(data,
                               geojson=districts,
                               locations='pc11_district_id',
                               color=var,
                               color_continuous_scale="YlGnBu_r",
                               range_color=(np.min(data[var]),
                                            np.max(data[var])),
                               featureidkey="properties.pc11_district_id",
                               opacity=0.5,
                               labels={var: label_dict[var]},
                              )

    fig.update_layout(mapbox_style="light",
                      mapbox_accesstoken=mapboxt,
                      mapbox_zoom=3,
                      mapbox_center = {"lat": 20.5937, "lon": 78.9629},
                      margin={"r":0,"t":0,"l":0,"b":0})
       
    all_vars.append(fig)
